In [1]:
import stable_baselines
from stable_baselines import A2C

The TensorFlow contrib module will not be included in TensorFlow 2.0.
For more information, please see:
  * https://github.com/tensorflow/community/blob/master/rfcs/20180907-contrib-sunset.md
  * https://github.com/tensorflow/addons
  * https://github.com/tensorflow/io (for I/O related ops)
If you depend on functionality not listed there, please file an issue.



/Users/akumaar/opt/anaconda3/envs/tf/lib/python3.7/site-packages/stable_baselines/__init__.py:33: UserWarning: stable-baselines is in maintenance mode, please use [Stable-Baselines3 (SB3)](https://github.com/DLR-RM/stable-baselines3) for an up-to-date version. You can find a [migration guide](https://stable-baselines3.readthedocs.io/en/master/guide/migration.html) in SB3 documentation.
  "stable-baselines is in maintenance mode, please use [Stable-Baselines3 (SB3)](https://github.com/DLR-RM/stable-baselines3) for an up-to-date version. You can find a [migration guide](https://stable-baselines3.readthedocs.io/en/master/guide/migration.html) in SB3 documentation."


In [2]:
import numpy as np
import pandas as pd

In [3]:
import gym
from gym.utils import seeding
from gym import spaces

In [4]:
merged_pools = pd.read_csv('/Users/akumaar/Downloads/test_data_date_index.csv')

In [23]:
training_df_final = pd.read_csv('/Users/akumaar/Downloads/training_df_final.csv')

In [ ]:
training_df_final = training_df_final.set_index(training_df_final.numspppp)
training_df_final

In [34]:
len(np.unique(training_df_final['stock_id']))

362

In [39]:
import numpy as np
import pandas as pd
from gym.utils import seeding
import gym
from gym import spaces
import matplotlib
matplotlib.use('Agg')
import matplotlib.pyplot as plt
import pickle

# shares normalization factor
# 100 shares per trade
HMAX_NORMALIZE = 100
# initial amount of money we have in our account
INITIAL_ACCOUNT_BALANCE=100000000
# total number of stocks in our portfolio
STOCK_DIM = 362
# transaction fee: 1/1000 percentage
TRANSACTION_FEE_PERCENT = 0.001
REWARD_SCALING = 1e-4

class StockEnvTrain(gym.Env):
    """A stock trading environment for OpenAI gym"""
    metadata = {'render.modes': ['human']}

    def __init__(self, df,day = 0):
        #super(StockEnv, self).__init__()
        #money = 10 , scope = 1
        self.day = day
        self.df = df

        # action_space normalization and shape is STOCK_DIM
        self.action_space = spaces.Box(low = -1, high = 1,shape = (STOCK_DIM,)) 
        # Shape = 709: [Current Balance]+[prices 1-236]+[owned shares 1-236] 
        # +[feature 1-236]
        self.observation_space = spaces.Box(low=0, high=np.inf, shape = (4345,))
        # load data from a pandas dataframe
        self.data = self.df.loc[self.day,:]
        self.terminal = False             
        # initalize state
        self.state = [INITIAL_ACCOUNT_BALANCE] + \
                      self.data.close.values.tolist() + \
                      [0]*STOCK_DIM + \
                      self.data.percent_good_subfund.values.tolist()+ \
                      self.data.x21.values.tolist() +\
                      self.data.x1.values.tolist() +\
                      self.data['good fund'].values.tolist() +\
                      self.data['irisk'].values.tolist() +\
                      self.data['x20'].values.tolist() +\
                      self.data['x4'].values.tolist() +\
                      self.data['1M Return'].values.tolist() +\
                      self.data['2M Return'].values.tolist() +\
                      self.data['3M Return'].values.tolist()
                      
        # initialize reward
        self.reward = 0
        self.cost = 0
        # memorize all the total balance change
        self.asset_memory = [INITIAL_ACCOUNT_BALANCE]
        self.rewards_memory = []
        self.trades = 0
        #self.reset()
        self.date_memory=[self.data.date.unique()[0]]
        self._seed()


    def _sell_stock(self, index, action):
        # perform sell action based on the sign of the action
        if self.state[index+STOCK_DIM+1] > 0:
            #update balance
            self.state[0] += \
            self.state[index+1]*min(abs(action),self.state[index+STOCK_DIM+1]) * \
             (1- TRANSACTION_FEE_PERCENT)

            self.state[index+STOCK_DIM+1] -= min(abs(action), self.state[index+STOCK_DIM+1])
            self.cost +=self.state[index+1]*min(abs(action),self.state[index+STOCK_DIM+1]) * \
             TRANSACTION_FEE_PERCENT
            self.trades+=1
        else:
            pass

    
    def _buy_stock(self, index, action):
        # perform buy action based on the sign of the action
        available_amount = self.state[0] // self.state[index+1]
        # print('available_amount:{}'.format(available_amount))

        #update balance
        self.state[0] -= self.state[index+1]*min(available_amount, action)* \
                          (1+ TRANSACTION_FEE_PERCENT)

        self.state[index+STOCK_DIM+1] += min(available_amount, action)

        self.cost+=self.state[index+1]*min(available_amount, action)* \
                          TRANSACTION_FEE_PERCENT
        self.trades+=1
        
    def step(self, actions):
        # print(self.day)
        self.terminal = self.day >= len(self.df.index.unique())-1
        # print(actions)

        if self.terminal:
            plt.plot(self.asset_memory,'r')
            #plt.savefig('results/account_value_train.png')
            plt.close()
            end_total_asset = self.state[0]+ \
            sum(np.array(self.state[1:(STOCK_DIM+1)])*np.array(self.state[(STOCK_DIM+1):(STOCK_DIM*2+1)]))
            
            #print("end_total_asset:{}".format(end_total_asset))
            df_total_value = pd.DataFrame(self.asset_memory)
           # df_total_value.to_csv('results/account_value_train.csv')
            #print("total_reward:{}".format(self.state[0]+sum(np.array(self.state[1:(STOCK_DIM+1)])*np.array(self.state[(STOCK_DIM+1):61]))- INITIAL_ACCOUNT_BALANCE ))
            #print("total_cost: ", self.cost)
            #print("total_trades: ", self.trades)
            df_total_value.columns = ['account_value']
            df_total_value['daily_return']=df_total_value.pct_change(1)
            sharpe = (252**0.5)*df_total_value['daily_return'].mean()/ \
                  df_total_value['daily_return'].std()
            #print("Sharpe: ",sharpe)
            #print("=================================")
            df_rewards = pd.DataFrame(self.rewards_memory)
            
            return self.state, self.reward, self.terminal,{}

        else:
            # print(np.array(self.state[1:29]))

            actions = actions * HMAX_NORMALIZE
            #actions = (actions.astype(int))
            
            begin_total_asset = self.state[0]+ \
            sum(np.array(self.state[1:(STOCK_DIM+1)])*np.array(self.state[(STOCK_DIM+1):(STOCK_DIM*2+1)]))
            #print("begin_total_asset:{}".format(begin_total_asset))
            
            argsort_actions = np.argsort(actions)
            
            sell_index = argsort_actions[:np.where(actions < 0)[0].shape[0]]
            buy_index = argsort_actions[::-1][:np.where(actions > 0)[0].shape[0]]

            for index in sell_index:
                # print('take sell action'.format(actions[index]))
                self._sell_stock(index, actions[index])

            for index in buy_index:
                # print('take buy action: {}'.format(actions[index]))
                self._buy_stock(index, actions[index])

            self.day += 1
            self.data = self.df.loc[self.day,:]         
            #load next state
            #print("stock_shares:{}".format(self.state[29:]))
            self.state =  [self.state[0]] + \
                    self.data.close.values.tolist() + \
                    list(self.state[(STOCK_DIM+1):(STOCK_DIM*2+1)]) + \
                    self.data.percent_good_subfund.values.tolist()+ \
                    self.data.x21.values.tolist() +\
                    self.data.x1.values.tolist() +\
                    self.data['good fund'].values.tolist() +\
                    self.data['irisk'].values.tolist() +\
                    self.data['x20'].values.tolist() +\
                    self.data['x4'].values.tolist() +\
                    self.data['1M Return'].values.tolist() +\
                    self.data['2M Return'].values.tolist() +\
                    self.data['3M Return'].values.tolist()
                   
            
            end_total_asset = self.state[0]+ \
            sum(np.array(self.state[1:(STOCK_DIM+1)])*np.array(self.state[(STOCK_DIM+1):(STOCK_DIM*2+1)]))
            self.asset_memory.append(end_total_asset)
            print("end_total_asset:{}".format(end_total_asset))
            
            self.reward = end_total_asset - begin_total_asset            
            print("step_reward:{}".format(self.reward))
            self.rewards_memory.append(self.reward)
            
            self.reward = self.reward*REWARD_SCALING

            self.date_memory.append(self.data.date.unique()[0])            


        return self.state, self.reward, self.terminal, {}

    def reset(self):
        self.asset_memory = [INITIAL_ACCOUNT_BALANCE]
        self.day = 0
        self.data = self.df.loc[self.day,:]
        self.cost = 0
        self.trades = 0
        self.terminal = False 
        self.rewards_memory = []
        #initiate state
        self.state = [INITIAL_ACCOUNT_BALANCE] + \
                      self.data.close.values.tolist() + \
                      [0]*STOCK_DIM + \
                      self.data.percent_good_subfund.values.tolist() + \
                      self.data.x21.values.tolist() +\
                      self.data.x1.values.tolist() +\
                      self.data['good fund'].values.tolist() +\
                      self.data['irisk'].values.tolist() +\
                      self.data['x20'].values.tolist() +\
                      self.data['x4'].values.tolist() +\
                      self.data['1M Return'].values.tolist() +\
                      self.data['2M Return'].values.tolist() +\
                      self.data['3M Return'].values.tolist()
        self.date_memory=[self.data.date.unique()[0]] 

        # iteration += 1 
        return self.state
    
    def render(self, mode='human'):
        return self.state
    def get_sb_env(self):
        e = DummyVecEnv([lambda: self])
        obs = e.reset()
        return e, obs
    def softmax_normalization(self, actions):
        numerator = np.exp(actions)
        denominator = np.sum(np.exp(actions))
        softmax_output = numerator/denominator
        return softmax_output

    
    def save_asset_memory(self):
        date_list = self.date_memory
        portfolio_return = self.asset_memory
        #print(len(date_list))
        #print(len(asset_list))
        df_account_value = pd.DataFrame({'date':date_list,'daily_return':portfolio_return})
        return df_account_value

    def save_action_memory(self):
        # date and close price length must match actions length
        date_list = self.date_memory
        df_date = pd.DataFrame(date_list)
        df_date.columns = ['date']
        
        action_list = self.actions_memory
        df_actions = pd.DataFrame(action_list)
        df_actions.columns = self.data.tic.values
        df_actions.index = df_date.date
        #df_actions = pd.DataFrame({'date':date_list,'actions':action_list})
        return df_actions
    def _seed(self, seed=None):
        self.np_random, seed = seeding.np_random(seed)
        return [seed]

In [ ]:
from stable_baselines import A2C

import tensorflow
from stable_baselines.common.policies import MlpPolicy, MlpLstmPolicy, MlpLnLstmPolicy
from stable_baselines.common.noise import NormalActionNoise, OrnsteinUhlenbeckActionNoise, AdaptiveParamNoiseSpec
from stable_baselines.common.vec_env import DummyVecEnv
import time

def train_A2C(env_train, timesteps=10000):
    start = time.time()
    model = A2C('MlpPolicy', env_train, verbose=1)
    model.learn(total_timesteps=timesteps)
    end = time.time()
    print('Training time (A2C): ', (end-start)/60,' minutes')
    return model

In [6]:
merged_pools1 = merged_pools[merged_pools['date']<'2017-12-31']

In [7]:
merged_pools1 = merged_pools1.set_index('nums')

In [40]:
env = StockEnvTrain(training_df_final)

In [ ]:
train_A2C(env)

In [ ]:
def DRL_prediction(df,
                   model,
                   name,
                   last_state,
                   iter_num,
                   unique_trade_date,
                   rebalance_window,
                   initial):
    ### make a prediction based on trained model###

    ## trading env
    trade_data = data_split(df, start=unique_trade_date[iter_num - rebalance_window], end=unique_trade_date[iter_num])
    env_trade = DummyVecEnv([lambda: StockEnvTrain(trade_data,
                                                   initial=initial,
                                                   previous_state=last_state,
                                                   model_name=name,
                                                   iteration=iter_num)])
    obs_trade = env_trade.reset()

    for i in range(len(trade_data.index.unique())):
        action, _states = model.predict(obs_trade)
        obs_trade, rewards, dones, info = env_trade.step(action)
        if i == (len(trade_data.index.unique()) - 2):
            # print(env_test.render())
            last_state = env_trade.render()

    df_last_state = pd.DataFrame({'last_state': last_state})
    df_last_state.to_csv('results/last_state_{}_{}.csv'.format(name, i), index=False)
    return last_state


In [ ]:
##Below: The validation methods from FinRL_portfolio_allocation_NeurIPS_2020 github
#https://github.com/AI4Finance-LLC/FinRL/blob/master/FinRL_portfolio_allocation_NeurIPS_2020.ipynb

In [9]:
from finrl.drl_agents.stablebaselines3.models import DRLAgent

In [41]:
agent = DRLAgent(env = env)

A2C_PARAMS = {"n_steps": 5, "ent_coef": 0.005, "learning_rate": 0.0002}
model_a2c = agent.get_model(model_name="a2c",model_kwargs = A2C_PARAMS)

{'n_steps': 5, 'ent_coef': 0.005, 'learning_rate': 0.0002}
Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.


In [42]:
trained_a2c = agent.train_model(model=model_a2c, 
                                tb_log_name='a2c',
                                total_timesteps=50000)

Logging to tensorboard_log/a2c/a2c_6
end_total_asset:100187992.37307921
step_reward:187992.37307921052
end_total_asset:100127924.04445048
step_reward:-60068.328628733754
end_total_asset:99967895.62154512
step_reward:-160028.4229053557
end_total_asset:100293325.27140729
step_reward:325429.6498621702
end_total_asset:99984256.35872455
step_reward:-309068.9126827419
end_total_asset:100282787.68488318
step_reward:298531.32615862787
end_total_asset:100162122.82986093
step_reward:-120664.8550222516
end_total_asset:100007131.11930197
step_reward:-154991.7105589509
end_total_asset:99916348.02716531
step_reward:-90783.09213666618
end_total_asset:101177887.0854669
step_reward:1261539.0583015978
end_total_asset:99982400.97493623
step_reward:-1195486.1105306745
end_total_asset:100209339.49111348
step_reward:226938.51617725194
end_total_asset:100453394.11779463
step_reward:244054.626681149
end_total_asset:100732283.74473777
step_reward:278889.6269431412
end_total_asset:100117451.42249383
step_reward

end_total_asset:100013725.02470116
step_reward:13725.024701163173
end_total_asset:100302142.5661732
step_reward:288417.54147203267
end_total_asset:100159714.77380744
step_reward:-142427.7923657596
end_total_asset:100196875.60730024
step_reward:37160.83349280059
end_total_asset:100334242.50380273
step_reward:137366.8965024948
end_total_asset:100630810.87688789
step_reward:296568.3730851561
end_total_asset:100771003.54455048
step_reward:140192.66766259074
end_total_asset:100671960.75137988
step_reward:-99042.79317060113
end_total_asset:101136464.02978873
step_reward:464503.2784088552
end_total_asset:101622561.95284075
step_reward:486097.9230520129
end_total_asset:101040310.96908674
step_reward:-582250.983754009
end_total_asset:101503869.95369847
step_reward:463558.98461173475
end_total_asset:101799779.13664754
step_reward:295909.18294906616
end_total_asset:101556728.39450742
step_reward:-243050.7421401143
end_total_asset:99954201.09486404
step_reward:-45798.90513595939
end_total_asset:10

end_total_asset:99944561.15778087
step_reward:-55438.842219129205
end_total_asset:99911395.013672
step_reward:-33166.144108876586
end_total_asset:100062028.71025717
step_reward:150633.69658517838
end_total_asset:99841120.54041468
step_reward:-220908.1698424965
end_total_asset:100259662.32205816
step_reward:418541.78164348006
end_total_asset:100317663.93715659
step_reward:58001.61509843171
end_total_asset:100263735.76549318
step_reward:-53928.17166340351
end_total_asset:100101732.48514853
step_reward:-162003.28034465015
end_total_asset:100041571.54914947
step_reward:-60160.93599906564
end_total_asset:100830373.47544926
step_reward:788801.9262997955
end_total_asset:100750152.2462499
step_reward:-80221.22919936478
end_total_asset:100595419.98716731
step_reward:-154732.25908258557
end_total_asset:101222983.74426845
step_reward:627563.7571011335
end_total_asset:102317876.96074007
step_reward:1094893.2164716274
end_total_asset:100061345.47002068
step_reward:61345.47002068162
end_total_asset:

end_total_asset:101011954.40073697
step_reward:991960.768066302
end_total_asset:100424320.91635028
step_reward:-587633.4843866974
end_total_asset:100939129.79027289
step_reward:514808.87392261624
end_total_asset:101619855.13500793
step_reward:680725.3447350413
end_total_asset:101086089.96545357
step_reward:-533765.1695543677
end_total_asset:100784024.02759446
step_reward:-302065.9378591031
end_total_asset:100021094.91265596
step_reward:21094.912655964494
end_total_asset:100104179.40039936
step_reward:83084.48774339259
end_total_asset:100463042.88066883
step_reward:358863.4802694768
end_total_asset:100445469.76484518
step_reward:-17573.11582365632
end_total_asset:100721089.11318932
step_reward:275619.3483441472
end_total_asset:101107843.08012903
step_reward:386753.96693970263
end_total_asset:100606269.40940858
step_reward:-501573.67072044313
end_total_asset:100619869.62319471
step_reward:13600.213786125183
end_total_asset:100605848.58381562
step_reward:-14021.03937909007
end_total_asset

end_total_asset:100056082.46263121
step_reward:56082.462631210685
end_total_asset:100196859.17613028
step_reward:140776.7134990692
end_total_asset:100295473.19909504
step_reward:98614.02296476066
end_total_asset:100053498.0281044
step_reward:-241975.1709906459
end_total_asset:100553603.67688814
step_reward:500105.6487837434
end_total_asset:100725581.82257038
step_reward:171978.1456822455
end_total_asset:100784124.85473666
step_reward:58543.0321662724
end_total_asset:100582878.64011279
step_reward:-201246.21462386847
end_total_asset:100317551.60280553
step_reward:-265327.0373072624
end_total_asset:100918060.50075853
step_reward:600508.8979530036
end_total_asset:100638405.07321419
step_reward:-279655.4275443405
end_total_asset:101015721.9272134
step_reward:377316.8539992124
end_total_asset:102101870.93447937
step_reward:1086149.00726597
end_total_asset:102415436.75031632
step_reward:313565.81583695114
end_total_asset:100122692.77975248
step_reward:122692.779752478
end_total_asset:1001310

...

end_total_asset:101361409.23650017
step_reward:-83295.79597236216
end_total_asset:101792699.40495975
step_reward:431290.16845957935
end_total_asset:102249811.82074489
step_reward:457112.41578513384
end_total_asset:101589159.2300232
step_reward:-660652.5907216817
end_total_asset:101988643.78522047
step_reward:399484.5551972687
end_total_asset:103034377.50071616
step_reward:1045733.7154956907
end_total_asset:100161113.2786671
step_reward:161113.27866710722
end_total_asset:100413964.49382278
step_reward:252851.215155676
end_total_asset:100710000.7963862
step_reward:296036.302563414
end_total_asset:100614870.19164301
step_reward:-95130.60474318266
end_total_asset:101215444.49968654
step_reward:600574.3080435246
end_total_asset:101079746.4236587
step_reward:-135698.07602784038
end_total_asset:101403936.92669404
step_reward:324190.50303533673
end_total_asset:101867994.99528635
step_reward:464058.06859230995
end_total_asset:101832688.18778142
step_reward:-35306.80750492215
end_total_asset:103

end_total_asset:101500264.82787016
step_reward:454205.81908755004
end_total_asset:101508995.54032019
step_reward:8730.712450027466
end_total_asset:101119131.3181745
step_reward:-389864.2221456915
end_total_asset:102250408.8159688
step_reward:1131277.4977943003
end_total_asset:102126326.18020025
step_reward:-124082.63576854765
end_total_asset:102218176.69458425
step_reward:91850.5143840015
end_total_asset:102491238.23546782
step_reward:273061.5408835709
end_total_asset:103683080.84259515
step_reward:1191842.6071273237
end_total_asset:100156503.0352402
step_reward:156503.03524020314
end_total_asset:100176185.66122665
step_reward:19682.62598644197
end_total_asset:100434651.38398482
step_reward:258465.72275817394
end_total_asset:100452181.58541162
step_reward:17530.201426804066
end_total_asset:100659541.91371821
step_reward:207360.32830658555
end_total_asset:101142956.33370605
step_reward:483414.41998784244
end_total_asset:101108260.31474583
step_reward:-34696.0189602226
end_total_asset:10

end_total_asset:101313298.91765329
step_reward:509340.9483040422
end_total_asset:101737300.15362298
step_reward:424001.23596969247
end_total_asset:101544063.16046414
step_reward:-193236.9931588471
end_total_asset:102334970.6345728
step_reward:790907.4741086662
end_total_asset:101973551.42205961
step_reward:-361419.2125131935
end_total_asset:102074134.0076595
step_reward:100582.58559988439
end_total_asset:103685002.0170256
step_reward:1610868.00936611
end_total_asset:104094599.22280489
step_reward:409597.20577928424
end_total_asset:100155668.92571938
step_reward:155668.92571938038
end_total_asset:100166933.91648525
step_reward:11264.990765869617
end_total_asset:100528048.23949659
step_reward:361114.3230113387
end_total_asset:100435142.77129872
step_reward:-92905.46819786727
end_total_asset:101292874.11772883
step_reward:857731.346430108
end_total_asset:101100814.9723009
step_reward:-192059.14542792737
end_total_asset:101216386.04693305
step_reward:115571.07463215292
end_total_asset:1012

end_total_asset:104094440.29403576
step_reward:1790107.3717418164
end_total_asset:100117067.9396748
step_reward:117067.93967479467
end_total_asset:100231563.77787162
step_reward:114495.83819682896
end_total_asset:100333128.9342526
step_reward:101565.1563809812
end_total_asset:100374136.28157192
step_reward:41007.347319319844
end_total_asset:101097061.57004882
step_reward:722925.2884768993
end_total_asset:100981178.76465599
step_reward:-115882.80539283156
end_total_asset:101059601.81863922
step_reward:78423.05398322642
end_total_asset:100724362.89182028
step_reward:-335238.92681893706
end_total_asset:101016500.38840564
step_reward:292137.4965853542
end_total_asset:101686016.46557277
step_reward:669516.0771671385
end_total_asset:101654471.80632123
step_reward:-31544.6592515409
end_total_asset:101722188.92699113
step_reward:67717.12066990137
end_total_asset:102127131.02848455
step_reward:404942.1014934182
end_total_asset:103227470.84255032
step_reward:1100339.8140657693
end_total_asset:10

end_total_asset:102494398.30321124
step_reward:1133849.005768299
end_total_asset:101756168.67230251
step_reward:-738229.6309087276
end_total_asset:102340193.23221725
step_reward:584024.5599147379
end_total_asset:102491381.82476568
step_reward:151188.59254842997
end_total_asset:104270356.1775446
step_reward:1778974.3527789116
end_total_asset:100156824.86594443
step_reward:156824.86594443023
end_total_asset:100176669.6877374
step_reward:19844.821792975068
end_total_asset:100391666.16238077
step_reward:214996.47464336455
end_total_asset:100492017.3829951
step_reward:100351.22061432898
end_total_asset:101187587.17641942
step_reward:695569.7934243232
end_total_asset:101275511.6215879
step_reward:87924.44516848028
end_total_asset:101440908.25001864
step_reward:165396.62843073905
end_total_asset:101470781.51935823
step_reward:29873.269339591265
end_total_asset:101661272.12601376
step_reward:190490.60665552318
end_total_asset:102330840.33737211
step_reward:669568.2113583535
end_total_asset:102

In [ ]:
quarterly_returns = DRLAgent.DRL_prediction(model = trained_a2c, environment = env)

In [21]:
merged_pools1

stock_id  percent_good_subfund        date    close
nums                                                      
0     001055102              2.978489  2013-09-30   30.995
0     00206R102              7.539118  2013-09-30   33.820
0     002824100              4.139970  2013-09-30   33.190
0     00287Y109              3.548546  2013-09-30   44.730
0     00507V109              0.426743  2013-09-30   16.680
...         ...                   ...         ...      ...
14    98978V103              1.330705  2017-06-30   62.380
14    G1151C101              3.474320  2017-06-30  123.680
14    G29183103              1.409922  2017-06-30   77.830
14    N6596X109              1.661631  2017-06-30  109.450
14    V7780T103              0.823045  2017-06-30  109.230

[3540 rows x 4 columns]